# Clusterlogs Notebook

In [1]:
import pandas as pd
from clusterlogs import multistage

### 1. Download data from file and create pandas DataFrame with index 

In [10]:
df = pd.read_csv('test/Project.csv', header=None)

In [21]:
df.dropna(inplace=True)

In [23]:
df.shape

(198832, 1)

In [17]:
df = pd.read_csv('test/test_data.csv', index_col=0)

In [2]:
df = pd.read_csv('samples/fts_mess_panda.csv', index_col=0).set_index('id')

In [25]:
df.head()

pandaid            starttime  exeerrorcode  \
0  4498866929  2019-10-01T09:04:39            65   
1  4498851809  2019-10-01T09:13:17            11   
2  4499004301  2019-10-01T10:18:49            15   
3  4499011565  2019-10-01T10:25:17            65   
4  4499004297  2019-10-01T10:15:46            15   

                                        exeerrordiag  \
0  Non-zero return code from EVNTtoHITS (8); Logf...   
1  Missing AthenaMP outputs file athenaMP-outputs...   
2  No events to process: 16000 (skipEvents) >= 23...   
3  Non-zero return code from AODtoDAOD (8); Logfi...   
4  No events to process: 14000 (skipEvents) >= 23...   

                                             cleaned  \
0  Non-zero return code from EVNTtoHITS (*); Logf...   
1  Missing AthenaMP outputs file * (probably athe...   
2  No events to process: * (skipEvents) >= * (inp...   
3  Non-zero return code from AODtoDAOD (*); Logfi...   
4  No events to process: * (skipEvents) >= * (inp...   

                                           tokenized  cluster_1 cluster_2  
0  [Non-zero, return, code, from, EVNTtoHITS, (, ...          0         0  
1  [Missing, AthenaMP, outputs, file, *, (, proba...          1         9  
2  [No, events, to, process, :, *, (, skipEvents,...          2        14  
3  [Non-zero, return, code, from, AODtoDAOD, (, *...          3         0  
4  [No, events, to, process, :, *, (, skipEvents,...          2        14

In [4]:
df.shape

(315761, 2)

### 2. Initialize clusterization pipeline

In [24]:
target = 0

In [ ]:
cluster = multistage.exec(df, target, 'undrus_logs.model')

### 3. Execute clusterization pipeline

In [7]:
cluster.process()

/Users/maria/PyCharmProjects/ClusterLogs/clusterlogs/pipeline.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.df['cleaned'] = self.messages_cleaned
/Users/maria/PyCharmProjects/ClusterLogs/clusterlogs/pipeline.py:129: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.df['tokenized_wordpunct'] = self.tokens.tokenized_wordpunct
/Users/maria/PyCharmProjects/ClusterLogs/clusterlogs/pipeline.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .l

In [8]:
cluster.timings

{'data_preparation': 1.4719,
 'tokenization': 0.9859,
 'tokens_vectorization': 0.1913,
 'sentence_vectorization': 9.7729,
 'dimensionality_reduction': 0.0495,
 'hdbscan': 0.1103,
 'extract_patterns': 0.8994,
 'reprocess': 18.2343,
 'statistics': 0.5102,
 'process': 32.2257}

In [9]:
len(cluster.tokens.wordpunct_vocab)

2905

In [10]:
len(cluster.tokens.pyonmttok_vocab)

5090

In [11]:
cluster.df['cluster_2'].unique()

array(['56', '61', '59', '60', '44', '8', '47', '53', '46', '57', '45',
       '58', '2', '52', '51', '63', '65', '40', '1', '7', '28', '55',
       '41', '62', '42', '23', '22', '34', '15', '64', '35', '37', '54',
       '13', '49', '48', '3', '33', '26', '6', '43', '21', '31', '38',
       '24', '9', '10', '12', '50', '11', '0', '20', '14', '16', '25',
       '4', '36', '5', '30', '29', '32', '27', '39', '19', '18', '17'],
      dtype=object)

In [15]:
cluster.patterns_stats.to_csv('patterns_stats_DBSCAN.csv')

In [16]:
cluster.results[['cluster_name','pattern','cluster_size','mean_similarity']].to_csv('day_log_DBSCAN.csv')

In [13]:
sum(cluster.results['cluster_size'])

315761

In [14]:
cluster.results.sort_values(by=['cluster_size'])

cluster_name  cluster_size  \
65            9             1   
63            7             1   
0             0             1   
45            5             1   
34            4             1   
..          ...           ...   
61           64           234   
62           65           262   
12            2           324   
64            8           633   
52           56          1089   

                                              pattern  \
65  # CMake ---> /*/atnight/localbuilds/nightlies/...   
63   void PlotView::resizeEvent (QResizeEvent *eve...   
0                                        # Dummy file   
45                          m_alignModuleMaps size: *   
34                  Warning: Unused variable rule: **   
..                                                ...   
61  # CMake ---> /cvmfs/sft.cern.ch/lcg/releases/g...   
62  # CMake ---> /cvmfs/sft.cern.ch/lcg/releases/g...   
12                            ^~~~~~~~~~~~~~~~~~~~~~~   
64  clid.db clid.db will be written to /*/atnight/...   
52  # CMake ---> /cvmfs/atlas.cern.ch/repo/ATLASLo...   

                                             sequence  mean_similarity  \
65  [#, CMake, --->, /*/atnight/localbuilds/nightl...             1.00   
63  [void, PlotView::resizeEvent, (QResizeEvent, *...             1.00   
0                                    [#, Dummy, file]             1.00   
45                      [m_alignModuleMaps, size:, *]             1.00   
34            [Warning:, Unused, variable, rule:, **]             1.00   
..                                                ...              ...   
61  [#, CMake, --->, /cvmfs/sft.cern.ch/lcg/releas...             0.51   
62  [#, CMake, --->, /cvmfs/sft.cern.ch/lcg/releas...             0.58   
12                          [^~~~~~~~~~~~~~~~~~~~~~~]             0.36   
64  [clid.db, clid.db, will, be, written, to, /*/a...             0.07   
52  [#, CMake, --->, /cvmfs/atlas.cern.ch/repo/ATL...             0.76   

    std_similarity  
65            0.00  
63            0.00  
0             0.00  
45            0.00  
34            0.00  
..             ...  
61            0.09  
62            0.11  
12            0.48  
64            0.21  
52            0.12  

[66 rows x 6 columns]

In [13]:
cluster.results[['pattern']].values

array([['# CMake ---> /cvmfs/atlas.cern.ch/repo/ATLASLocalRootBase/*/Cmake/*/*/bin/cmake -E make_directory /*/atnight/localbuilds/nightlies/*/build/build/Athena/*/include'],
       ['clid.db clid.db will be written to /*/atnight/localbuilds/nightlies/*/build/build/Athena/LArCalorimeter/LArGeoModel/LArGeoAlgsNV/LArGeoAlgsNV_clid.db.'],
       ['^~~~~~~~~~~~~~~~~~~~~~~'],
       ['# CMake ---> /cvmfs/sft.cern.ch/lcg/releases/gcc/*/*/bin/g++ -DATLAS * * -DCLHEP_MAX_MIN_DEFINED -DCLHEP_SQR_DEFINED -DHAVE_PRETTY_FUNCTION -DPACKAGE_VERSION="*" -DHAVE_GAUDI_PLUGINSVC -DHAVE_PRETTY_FUNCTION -isystem -fplugin=/*/atnight/localbuilds/nightlies/*/build/install/AthenaExternals/*/InstallArea/*/lib/libchecker_gccplugins.so -g -Wno-long-long -fplugin=/*/atnight/localbuilds/nightlies/*/build/install/AthenaExternals/*/InstallArea/*/lib/libchecker_gccplugins.so -fplugin=/*/atnight/localbuilds/nightlies/*/build/install/AthenaExternals/*/InstallArea/*/lib/libchecker_gccplugins.so -I/*/atnight/localbuilds/n

In [31]:
cluster.in_cluster(19,2).tolist()

['# CMake ---> /cvmfs/sft.cern.ch/lcg/releases/gcc/6.2.0-b9934/x86_64-slc6/bin/g++ -DATLAS -DATLAS_GAUDI_V21 -DCLHEP_ABS_DEFINED -DCLHEP_MAX_MIN_DEFINED -DCLHEP_SQR_DEFINED -DGAUDI_V20_COMPAT -DHAVE_64_BITS -DHAVE_GAUDI_PLUGINSVC -DHAVE_PRETTY_FUNCTION -DLArGeoAlgsNV_EXPORTS -DPACKAGE_VERSION="LArGeoAlgsNV-00-00-00" -DPACKAGE_VERSION_UQ=LArGeoAlgsNV-00-00-00 -D__IDENTIFIER_64BIT__ -I/build1/atnight/localbuilds/nightlies/21.0/athena/LArCalorimeter/LArGeoModel/LArGeoAlgsNV -I/build1/atnight/localbuilds/nightlies/21.0/athena/Control/IOVSvc -I/build1/atnight/localbuilds/nightlies/21.0/athena/Control/AthenaBaseComps -I/build1/atnight/localbuilds/nightlies/21.0/athena/Control/AthenaKernel -I/build1/atnight/localbuilds/nightlies/21.0/athena/Control/CxxUtils -I/build1/atnight/localbuilds/nightlies/21.0/athena/Control/DataModelRoot -I/build1/atnight/localbuilds/nightlies/21.0/build/install/GAUDI/21.0.105/InstallArea/x86_64-slc6-gcc62-dbg/include -I/build1/atnight/localbuilds/nightlies/21.0/athe

In [12]:
print(x)

[]


### 4. Get clusters statistics

In [8]:
output = cluster_output.Output(cluster.df, 
                               cluster.target)

In [9]:
mode = 'INDEX'

In [10]:
output.clustered_output(mode)
stats = output.statistics(output_mode='frame')

In [11]:
stats.sort_values(by=['mean_similarity'])

cluster_name  cluster_size  \
35            35             9   
65            65             9   
111          111             2   
41            41             3   
17            17             5   
..           ...           ...   
92            92             9   
58            58             9   
54            54             8   
42            42            10   
148          148             1   

                                               pattern  mean_length  \
35   Input file argument T globbed to NO input file...       100.78   
65   Failed in data staging: Failed checking source...       181.56   
111  Non-zero return code from OMerge (*); Logfile ...        95.00   
41   File DAOD_D*.*._*.pool.root.* did not pass cor...        62.33   
17   Non-zero return code from AODtoDAOD (*); Logfi...       129.40   
..                                                 ...          ...   
92   Non-zero return code from EVNTtoHITS (*); Logf...       126.00   
58   Non-zero return code from AODtoDAOD (*); Logfi...       116.00   
54   Fatal error in athena logfile: "Long ERROR mes...        97.00   
42   Non-zero return code from generate (*); Logfil...       138.00   
148  Non-zero return code from EVNTtoHITS (*); Logf...       103.00   

     mean_similarity  std_length  std_similarity  
35              0.90        3.99            0.03  
65              0.94        7.23            0.03  
111             0.94        2.00            0.00  
41              0.95        0.94            0.01  
17              0.95        3.20            0.03  
..               ...         ...             ...  
92              1.00        0.00            0.00  
58              1.00        0.00            0.00  
54              1.00        0.00            0.00  
42              1.00        0.00            0.00  
148             1.00        0.00            0.00  

[149 rows x 7 columns]

In [12]:
patterns = stats.sort_values(by='mean_similarity')[['pattern']].values

In [13]:
patterns

array([['Input file argument T globbed to NO input files - probably the file(s) are missing'],
       ['Failed in data staging: Failed checking source replica * Failed to obtain information about file: No such file or directory: Failed to stat file *_session******..b.'],
       ['Non-zero return code from OMerge (*); Logfile error in log.OMerge: "KeyError: \'nentries\'"'],
       ['File DAOD_D*.*._*.pool.root.* did not pass corruption test'],
       ['Non-zero return code from AODtoDAOD (*); Logfile error in log.AODtoDAOD: "* FATAL Standard std::exception is caught"'],
       ['Non-zero return code from generate (*); Logfile error in log.generate: "*: MadSpin was run but can\'t find output folder Events**_decayed_*"'],
       ['Non-zero return code from AODtoDAOD (*); Logfile error in log.AODtoDAOD: "* fault: Event counter: *; Run: *; Evt: *; Current algorithm: tag; Current Function: unknown"'],
       ['Fatal error in athena logfile: "Logfile error in log.toA: "ToolSvc.HLTJetMon ERROR

In [14]:
stats_1 = output.postprocessing(1)

In [15]:
stats_1.sort_values(by=['mean_similarity'])

cluster_name  cluster_size  \
0           0.0          1811   
2           2.0           205   
10         10.0             2   
7           7.0            61   
6           6.0            10   
4           4.0            36   
12         12.0           218   
5           5.0             7   
19         19.0          1141   
1           1.0             4   
13         13.0            38   
20         20.0            27   
3           3.0            97   
16         16.0           602   
27         27.0           427   
8           8.0             1   
14         14.0             2   
15         15.0             3   
17         17.0             8   
18         18.0             8   
25         25.0            18   
22         22.0            11   
23         23.0            14   
24         24.0            15   
11         11.0             1   
26         26.0            30   
28         28.0            84   
29         29.0           109   
21         21.0            10   
9           9.0             1   

                                              pattern  mean_length  \
0                      Non-zero return code from  (*)       122.31   
2           Fatal error in athena logfile: " eo in o"       122.61   
10  AODtoDAOD got a SIGKILL signal (exit code *); ...       134.50   
7   Nonet code *); o at line * (see jobReport for ...       104.56   
6   Failed in data staging: ld en source replica *...       180.40   
4                 File * did not pass corruption test        58.19   
12                               LRMS error: (*) Job         28.89   
5   Failed in data staging: Failed to prepare dest...       198.57   
19  Input file argument  globbed to NO input files...        99.07   
1                      Non-zero return code from  (*)        36.75   
13  Non-zero return code from  (*); Logfile error ...       168.32   
20             Eto got a SIGKILL signal (exit code *)        44.26   
3                  AOD got a SIG signal (exit code *)        43.98   
16  Missing AthenaMP outputs file * (probably athe...        60.31   
27  No events to process: * (skipEvents) >= * (inp...        62.00   
8   * got a SIGABRT signal (exit code *); Logfile ...        86.00   
14                      Job submission to LRMS failed        29.00   
15  AODtoDAOD got a SIGBUS signal (exit code *); L...       216.00   
17  Failed to clean up session dir before download...        56.00   
18  Fatal error in athena logfile: "Long ERROR mes...        97.00   
25                                             : ****         6.00   
22  Failed in data staging: Failed checking source...       115.00   
23                          Two identical output *: *        25.00   
24  Non-zero return code from generate (*); Logfil...       197.00   
11        Job was gone while performing data transfer        43.00   
26  Fatal error in athena logfile: "Logfile error ...       209.00   
28                              Data type graph error        21.00   
29      Error reading user generated output file list        45.00   
21  Event count check for EVNT to HITS failed: fou...       136.00   
9         generate got a SIGKILL signal (exit code *)        43.00   

    mean_similarity  std_length  std_similarity  
0              0.43       29.71            0.14  
2              0.53       28.78            0.11  
10             0.68        6.50            0.00  
7              0.76        1.25            0.06  
6              0.77        7.68            0.15  
4              0.80        5.07            0.04  
12             0.83        3.64            0.06  
5              0.84       28.71            0.08  
19             0.90        0.51            0.00  
1              0.91        3.34            0.06  
13             0.93        4.98            0.03  
20             0.93        0.97            0.03  
3              0.95        0.14            0.04  
16             0.97        4.85            0.04  
27             0.98        0.00            0.00  
8       

In [19]:
output.in_cluster(20,2)

array(['EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'ESDtoDPD got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIGKILL signal (exit code 137)',
       'EVNTtoHITS got a SIG

In [26]:
patterns1 = stats_1.sort_values(by='mean_similarity')[['pattern']].values

In [27]:
patterns1

array([['Non-zero return code from  (*)'],
       ['Non-zero return code from  (*); Logfile error in log.: "Eor: * u: *tretoOtion un'],
       ['Fatal error in athena logfile: "Logfile error in log.: "  e""'],
       ['AODtoDAOD got a SIGKILL signal (exit code *); Logfile error in log.AODtoDAOD: "* F tnrd oa"'],
       ['Failed in data staging: ld en source replica * ailed: No such file or directory: aid oat f'],
       ['Nonet code *); o at line * (see jobReport for further details)'],
       ['File * did not pass corruption test'],
       ['Failed in data staging: Failed to prepare destination * Failed to prepare destination: File exists: File requests have failed.: '],
       ['LRMS error: (*) Job '],
       ['Input file argument  globbed to NO input files - probably the file(s) are missing'],
       ['Non-zero return code from  (*)'],
       ['Eto got a SIGKILL signal (exit code *)'],
       ['Fatal error in athena logfile: "on at line * (see jobReport for further details)"'],
    

In [15]:
import difflib

In [16]:
sorted_df = output.stat_df.sort_values(by=['cluster_size'])[['cluster_size','cluster_name','pattern']]

In [135]:
sorted_df

cluster_size cluster_name  \
149             1          149   
138             1          138   
136             1          136   
139             1          139   
140             1          140   
..            ...          ...   
29            140           29   
13            385           13   
10            549           10   
20            805           20   
62           1098           62   

                                               pattern  
149  Non-zero return code from EVNTtoHITS (*); Logf...  
138  Non-zero return code from * (*); Logfile error...  
136  Non-zero return code from ESDtoAOD (*); Logfil...  
139  Non-zero return code from * (*); Logfile error...  
140  Non-zero return code from * (*); Logfile error...  
..                                                 ...  
29            Non-zero return code from EVNTtoHITS (*)  
13   No events to process: * (skipEvents) >= * (inp...  
10   Missing AthenaMP outputs file **r (probably at...  
20   Non-zero return code from AODtoDAOD (*); Logfi...  
62   Input file argument ${IN_MINBIAS_LOW/L} globbe...  

[150 rows x 3 columns]

In [136]:
def match(df, new_clusters):
    start = df.head(1)['pattern'].values[0]
#     print(start)
    ratio = [difflib.SequenceMatcher(None, start, x).ratio() for x in df['pattern']]
    df['ratio'] = ratio
    filtered = df[df['ratio'] > 0.6]['cluster_name'].values
    new_clusters.append(filtered)
#     print(filtered)
    df.drop(df[df['cluster_name'].isin(filtered)].index, inplace=True)
#     print(df)
    while df.shape[0] > 0:
        match(df, new_clusters)

In [137]:
new_clusters = []
# start = sorted_df.head(1)['pattern'].values[0]
# print(start)
match(sorted_df, new_clusters)

In [140]:
new_clusters

[array(['149', '136', '139', '133', '142', '143', '146', '144', '123',
        '105', '102', '51', '87', '79', '73', '72', '118', '112', '106',
        '48', '122', '109', '110', '108', '59', '90', '17', '3', '58',
        '93', '1', '36', '70', '39', '52', '74', '37', '24', '14', '45',
        '19'], dtype=object),
 array(['138', '97', '25', '86', '85', '9', '57'], dtype=object),
 array(['140'], dtype=object),
 array(['141', '117', '76', '67', '23', '28'], dtype=object),
 array(['135', '148', '30', '29'], dtype=object),
 array(['134', '81', '80'], dtype=object),
 array(['132', '95'], dtype=object),
 array(['131', '128', '91', '22'], dtype=object),
 array(['145', '137', '88'], dtype=object),
 array(['130', '84', '82', '101'], dtype=object),
 array(['129'], dtype=object),
 array(['127', '21', '99'], dtype=object),
 array(['126'], dtype=object),
 array(['124', '41', '8', '32', '26'], dtype=object),
 array(['107'], dtype=object),
 array(['120', '115', '69'], dtype=object),
 array(['121', 

In [145]:
a = []
for i in new_clusters:
    x = cluster.df[cluster.df['cluster'].isin(i)].index
    a.append({'cluster_name':i[-1],'idx':x})
print(a)

for i in a:
    cluster.df.loc[i['idx'], 'cluster_level_2'] = i['cluster_name']

[{'cluster_name': '19', 'idx': Int64Index([   2,    6,    7,    8,    9,   46,   59,   62,   63,   64,
            ...
            4861, 4874, 4875, 4897, 4912, 4915, 4937, 4949, 4956, 4967],
           dtype='int64', length=568)}, {'cluster_name': '57', 'idx': Int64Index([  50,   54,   55,  105,  275,  394,  580,  581,  645,  674,  914,
             923,  925,  926,  987,  993,  994, 1012, 1022, 1030, 1031, 1032,
            1037, 1246, 1268, 1343, 1389, 1555, 1843, 1845, 1863, 1944, 1948,
            1952, 1956, 1957, 1961, 2298, 2372, 2811, 2815, 2825, 2843, 2888,
            2913, 2915, 2926, 2932, 2933, 3022, 3251, 3524, 3572, 3763, 3772,
            3850, 3869, 3897, 3902, 3912, 4382, 4490, 4753, 4758, 4845, 4855,
            4883],
           dtype='int64')}, {'cluster_name': '140', 'idx': Int64Index([4037], dtype='int64')}, {'cluster_name': '28', 'idx': Int64Index([  90,  128,  260,  280,  290,  306,  408,  409,  410,  419,
            ...
            4374, 4390, 4403, 4405, 44

In [149]:
cluster.df['cluster_level_2'].describe()

count     5001
unique      43
top         62
freq      1141
Name: cluster_level_2, dtype: object

In [52]:
sorted_list = sorted_df['pattern'].tolist()

In [66]:
start = sorted_list[0]
print(start)
ratio = []
for x in sorted_list:
    ratio.append(difflib.SequenceMatcher(None, start, x).ratio())
print(ratio)
ids = [i for i,x in enumerate(ratio) if x > 0.6]
print(ids)

Non-zero return code from EVNTtoHITS (*); Logfile error in log.EVNTtoHITS: "StreamHITS FATAL * failed."
[1.0, 0.5638766519823789, 0.6181818181818182, 0.6272727272727273, 0.592057761732852, 0.1917808219178082, 0.44776119402985076, 0.4740740740740741, 0.6698113207547169, 0.6334841628959276, 0.32727272727272727, 0.4397163120567376, 0.6564102564102564, 0.3488372093023256, 0.39069767441860465, 0.2302158273381295, 0.5757575757575758, 0.3333333333333333, 0.5957446808510638, 0.6538461538461539, 0.17582417582417584, 0.15942028985507245, 0.663594470046083, 0.611353711790393, 0.5144927536231884, 0.5989304812834224, 0.455026455026455, 0.48, 0.2054794520547945, 0.5220588235294118, 0.39344262295081966, 0.5194805194805194, 0.273972602739726, 0.5886524822695035, 0.6255506607929515, 0.5841584158415841, 0.8682926829268293, 0.5517241379310345, 0.578397212543554, 0.5092250922509225, 0.784688995215311, 0.7159090909090909, 0.03289473684210526, 0.1793103448275862, 0.6666666666666666, 0.49122807017543857, 0.1

In [17]:
result = output.postprocessing()

In [19]:
result

matrix([[1.        , 0.18644068, 0.31446541, ..., 0.20979021, 0.19402985,
         0.1773399 ],
        [0.18644068, 1.        , 0.22564103, ..., 0.1452514 , 0.51973684,
         0.56903766],
        [0.33962264, 0.21538462, 1.        , ..., 0.23529412, 0.14977974,
         0.17283951],
        ...,
        [0.11188811, 0.16759777, 0.21568627, ..., 1.        , 0.14218009,
         0.20547945],
        [0.21641791, 0.53947368, 0.15859031, ..., 0.12322275, 1.        ,
         0.50922509],
        [0.1773399 , 0.56903766, 0.17283951, ..., 0.17808219, 0.50922509,
         1.        ]])

In [22]:
import numpy as np

In [27]:
threshold = 0.6
rows = np.where(result > threshold)

In [28]:
rows

(array([  0,   0,   0, ..., 149, 149, 149]),
 array([  0,  23,  51, ..., 139, 141, 149]))

In [20]:
similar

matrix([[1.        , 0.8159204 , 0.89010989, ..., 0.86829268, 0.62555066,
         1.        ]])

### Timings for all stages of clusterization pipeline

process - timing of all process

In [ ]:
cluster.timings

### Get all error messages in single cluster

In [ ]:
output.in_cluster(10)

In [ ]:
output.in_cluster(34)

### Output clusters - mode == 'ALL'  (for cluster '2')

In [ ]:
output.clustered_output(mode='ALL')['1']

### Output clusters - mode == 'INDEX' (for cluster '2')

In [ ]:
output.clustered_output(mode='INDEX')['1']

### Output clusters - mode == 'TARGET' (for cluster '2')

In [ ]:
output.clustered_output(mode='TARGET')['1']

### Output clusters - cluster labels

In [ ]:
cluster.cluster_labels

### Get epsilon value (which was used in DBSCAN algorithm)

In [ ]:
cluster.epsilon